In [ ]:
#try different models here

In [1]:
# Allowed to make changes.
import collections
import json
import pandas as pd
import requests
import re
import string
import timeit
from ast import literal_eval
# !pip install transformers

# !pip install git+https://github.com/deepset-ai/haystack.git
# !pip install urllib3==1.26.0
# from haystack.document_stores.elasticsearch import ElasticsearchDocumentStore
# from haystack.nodes import DensePassageRetriever
# from haystack.nodes import FARMReader
# from haystack.pipelines import ExtractiveQAPipeline

# from transformers import AutoModelForQuestionAnswering, AutoTokenizer, pipeline
# import torch
# device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
# ! wget https://artifacts.elastic.co/downloads/elasticsearch/elasticsearch-7.9.2-linux-x86_64.tar.gz -q
# ! tar -xzf elasticsearch-7.9.2-linux-x86_64.tar.gz
# ! chown -R daemon:daemon elasticsearch-7.9.2

# import os
# from subprocess import Popen, PIPE, STDOUT
# es_server = Popen(['elasticsearch-7.9.2/bin/elasticsearch'],
#                    stdout=PIPE, stderr=STDOUT,
#                    preexec_fn=lambda: os.setuid(1)  # as daemon
#                   )
# # wait until ES has started
# ! sleep 30

In [2]:
!pip install git+https://github.com/deepset-ai/haystack.git
!pip install urllib3==1.25.4
from haystack.document_stores.elasticsearch import ElasticsearchDocumentStore
from haystack.nodes import DensePassageRetriever
from haystack.nodes import FARMReader
from haystack.pipelines import ExtractiveQAPipeline

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/deepset-ai/haystack.git to /tmp/pip-req-build-z3y9uomn
  Running command git clone --filter=blob:none --quiet https://github.com/deepset-ai/haystack.git /tmp/pip-req-build-z3y9uomn
  Resolved https://github.com/deepset-ai/haystack.git to commit 9e457db2e96248e107c39ab78e5f8d6dbd75d755
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.0/386.0 KB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 228.4/228.4 KB 26.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.7/10.7 MB 81.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 KB 70.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 125.5/125.5 KB 4.0 MB/s eta 0:00:00
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.26.14
    Uninstalling urllib3-1.26.14:
      Successfully uninstalled urllib3-1.26.14
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
docker 6.0.1 requires urllib3>=1.26.0, but you have urllib3 1.25.4 which is incompatible.


In [3]:
! wget https://artifacts.elastic.co/downloads/elasticsearch/elasticsearch-7.9.2-linux-x86_64.tar.gz -q
! tar -xzf elasticsearch-7.9.2-linux-x86_64.tar.gz
! chown -R daemon:daemon elasticsearch-7.9.2

import os
from subprocess import Popen, PIPE, STDOUT
es_server = Popen(['elasticsearch-7.9.2/bin/elasticsearch'],
                   stdout=PIPE, stderr=STDOUT,
                   preexec_fn=lambda: os.setuid(1)  # as daemon
                  )
# wait until ES has started
! sleep 30

In [4]:
# from subprocess import Popen, PIPE, STDOUT
# es_server = Popen(['elasticsearch-7.9.2/bin/elasticsearch'],
#                    stdout=PIPE, stderr=STDOUT,
#                    preexec_fn=lambda: os.setuid(1)  # as daemon
#                   )
# # wait until ES has started
# ! sleep 30

In [5]:
!gdown 1Z-yb752A3o7b9dqrGt24XU0sl53FVqya
!gdown 1o1VCMOLmx7nTcztg4IG65ed2c0oxPqG4 # train_ground_truth.csv
!gdown 1Il8FjSe-2aYg9NhCqG2yGFU7FtLDfKp4 # train_input_paragraph.csv
!gdown 1-h0dcPiuEiWoseXrjRhj2Ru3wv9-p7aL # train_input_question.csv
!gdown 1DszAla41KYcYn3vRsyb6pgTbguIVLVD8 # train_theme_interval.csv

Downloading...
From: https://drive.google.com/uc?id=1Z-yb752A3o7b9dqrGt24XU0sl53FVqya
To: /content/train_data.csv
100% 65.6M/65.6M [00:00<00:00, 104MB/s] 
Downloading...
From: https://drive.google.com/uc?id=1o1VCMOLmx7nTcztg4IG65ed2c0oxPqG4
To: /content/train_ground_truth.csv
100% 2.23M/2.23M [00:00<00:00, 217MB/s]
Downloading...
From: https://drive.google.com/uc?id=1Il8FjSe-2aYg9NhCqG2yGFU7FtLDfKp4
To: /content/train_input_paragraph.csv
100% 12.0M/12.0M [00:00<00:00, 65.3MB/s]
Downloading...
From: https://drive.google.com/uc?id=1-h0dcPiuEiWoseXrjRhj2Ru3wv9-p7aL
To: /content/train_input_question.csv
100% 6.06M/6.06M [00:00<00:00, 158MB/s]
Downloading...
From: https://drive.google.com/uc?id=1DszAla41KYcYn3vRsyb6pgTbguIVLVD8
To: /content/train_theme_interval.csv
100% 9.88k/9.88k [00:00<00:00, 11.7MB/s]


In [8]:
# Allowed to make changes.
# Pre-processing cell. You can use this cell to pre-process input data or load
# your models.
train_input_paragraph= pd.read_csv('train_input_paragraph.csv')
paras=[]
for i in range(len(train_input_paragraph)):
  paras.append(train_input_paragraph.loc[i,'paragraph'])
data_json = [
    {
        'content': paragraph,
        'meta': {
            'theme': train_input_paragraph.loc[i,'theme']
        }
    } for i,paragraph in enumerate(paras)
]

doc_store = ElasticsearchDocumentStore(host="localhost", username="", password="", index="them")
doc_store.write_documents(data_json)

retriever1  = DensePassageRetriever(
    document_store=doc_store,
    query_embedding_model =  'facebook/dpr-question_encoder-single-nq-base',
    passage_embedding_model = 'facebook/dpr-ctx_encoder-single-nq-base',
    use_gpu = False,
    embed_title = True,
)
doc_store.update_embeddings(retriever=retriever1)
reader = FARMReader(model_name_or_path="deepset/tinyroberta-squad2", use_gpu=False)
pipe = ExtractiveQAPipeline(reader=reader, retriever=retriever1)

# model_name = "deepset/tinyroberta-squad2"  #choose model name
# nlp = pipeline('question-answering', model=model_name, tokenizer=model_name, device=device)
# Dummy code.
# paragraph_ds = []
# global_model = {}
def normalize_answer(s):
  """Lower text and remove punctuation, articles and extra whitespace."""
  def remove_articles(text):
    regex = re.compile(r'\b(a|an|the)\b', re.UNICODE)
    return re.sub(regex, ' ', text)
  def white_space_fix(text):
    return ' '.join(text.split())
  def remove_punc(text):
    exclude = set(string.punctuation)
    return ''.join(ch for ch in text if ch not in exclude)
  def lower(text):
    return text.lower()
  return white_space_fix(remove_articles(remove_punc(lower(s))))

Downloading:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/232k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/466k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/493 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/438M [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/383 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/798k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/456k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/239 [00:00<?, ?B/s]

In [9]:
# Allowed to make changes.
def get_theme_model(theme):
  # Here, you can load and return a model which is fine tuned for a theme.
  # In case, you only have a global model, you can return that.

  global_model= pipe
  return global_model

In [10]:
# Allowed to make changes.
theme_df= train_input_paragraph
ids=doc_store.get_document_by_id
def pred_theme_ans(questions, theme_model, pred_out):
  theme = questions[0]["theme"]
  reqtheme_df= theme_df[theme_df['theme']==theme].reset_index(drop=True)
  for step,question in enumerate(questions):

    ans = {}
    ans["question_id"] = question["id"]
    ques= normalize_answer(question['question'])

    ans['paragraph_id']= -1
    ans['answers']= " "

    prediction = pipe.run(query = ques , params={"Retriever":  {"filters" : {"theme" : str(theme)}}})
    pred= prediction['answers'][0]
    id= pred.document_id
    score= pred.score
    #change threshold here
    threshold=0.7

    if(score>=threshold):
      ans['answers']= pred.answer
      context= ids(id).content
      ans['paragraph_id']= reqtheme_df[theme_df['paragraph']==context].id.values[0]
    # best_score=0
    # flag=0
    # for i in range(len(reqtheme_df)):
    #   context= reqtheme_df.loc[i,'paragraph']
    #   context= normalize_answer(context)
    #   p= theme_model(context=context, question=ques)
      
    #   if p['score']>best_score and p['score']>threshold:
    #     ans['answers']= p['answer']
    #     ans['paragraph_id']= reqtheme_df.loc[i,'id']
    #     best_score=p['score']

    pred_out.append(ans)

In [ ]:
# NOT allowed to make changes. 

# All theme prediction.
questions = json.loads(pd.read_csv("train_input_question.csv").to_json(orient="records"))
theme_intervals = json.loads(pd.read_csv("train_theme_interval.csv").to_json(orient="records"))
pred_out = []
theme_inf_time = {}
for theme_interval in theme_intervals:
  theme_ques = questions[int(theme_interval["start"])-1: int(theme_interval["end"])]
  theme = theme_ques[0]["theme"]
  # Load model fine-tuned for this theme.
  theme_model = get_theme_model(theme)
  execution_time = timeit.timeit(lambda: pred_theme_ans(theme_ques, theme_model, pred_out), number=1)
  theme_inf_time[theme_interval["theme"]] = execution_time * 1000 # in milliseconds.
  break # remove this to calculate all themes

pred_df = pd.DataFrame.from_records(pred_out)
# Write prediction to a CSV file. Teams are required to submit this csv file.
pred_df.to_csv('train_output_prediction.csv', index=False)

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

<ipython-input-10-5c59a7a65648>:26: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  ans['paragraph_id']= reqtheme_df[theme_df['paragraph']==context].id.values[0]


Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

...

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

In [ ]:
pred_df.head()

In [ ]:
# NOT allowed to make changes. 

# def normalize_answer(s):
#   """Lower text and remove punctuation, articles and extra whitespace."""
#   def remove_articles(text):
#     regex = re.compile(r'\b(a|an|the)\b', re.UNICODE)
#     return re.sub(regex, ' ', text)
#   def white_space_fix(text):
#     return ' '.join(text.split())
#   def remove_punc(text):
#     exclude = set(string.punctuation)
#     return ''.join(ch for ch in text if ch not in exclude)
#   def lower(text):
#     return text.lower()
#   return white_space_fix(remove_articles(remove_punc(lower(s))))

# def get_tokens(s):
#   if not s: return []
#   return normalize_answer(s).split()

# def calc_f1(a_gold, a_pred):
#   gold_toks = get_tokens(a_gold)
#   pred_toks = get_tokens(a_pred)
#   common = collections.Counter(gold_toks) & collections.Counter(pred_toks)
#   num_same = sum(common.values())
#   if len(gold_toks) == 0 or len(pred_toks) == 0:
#     # If either is no-answer, then F1 is 1 if they agree, 0 otherwise
#     return int(gold_toks == pred_toks)
#   if num_same == 0:
#     return 0
#   precision = 1.0 * num_same / len(pred_toks)
#   recall = 1.0 * num_same / len(gold_toks)
#   f1 = (2 * precision * recall) / (precision + recall)
#   return f1

# def calc_max_f1(predicted, ground_truths):
#   max_f1 = 0
#   for ground_truth in ground_truths:
#     f1 = calc_f1(predicted, ground_truth)
#     max_f1 = max(max_f1, f1)
#   return max_f1

def normalize_answer(s):
  """Lower text and remove punctuation, articles and extra whitespace."""
  def remove_articles(text):
    regex = re.compile(r'\b(a|an|the)\b', re.UNICODE)
    return re.sub(regex, ' ', text)
  def white_space_fix(text):
    return ' '.join(text.split())
  def remove_punc(text):
    exclude = set(string.punctuation)
    return ''.join(ch for ch in text if ch not in exclude)
  def lower(text):
    return text.lower()
  return white_space_fix(remove_articles(remove_punc(lower(s))))

def get_tokens(s):
  if not s: return []
  return normalize_answer(s).split()

def calc_f1(a_gold, a_pred):
  gold_toks = get_tokens(str(a_gold))
  pred_toks = get_tokens(str(a_pred))
  common = collections.Counter(gold_toks) & collections.Counter(pred_toks)
  num_same = sum(common.values())
  if len(gold_toks) == 0 or len(pred_toks) == 0:
    # If either is no-answer, then F1 is 1 if they agree, 0 otherwise
    return int(gold_toks == pred_toks)
  if num_same == 0:
    return 0
  precision = 1.0 * num_same / len(pred_toks)
  recall = 1.0 * num_same / len(gold_toks)
  f1 = (2 * precision * recall) / (precision + recall)
  return f1

def calc_max_f1(predicted, ground_truths):
  max_f1 = 0
  if len(ground_truths)==0:
    max_f1= calc_f1(predicted, ground_truths)
  else:
    for ground_truth in ground_truths:
      f1 = calc_f1(predicted, ground_truth)
      max_f1 = max(max_f1, f1)
  return max_f1

In [ ]:
# NOT allowed to make changes. 

# Evaluation methodology.
metrics = {}
pred = pd.read_csv("train_output_prediction.csv")
truth = pd.read_csv("train_ground_truth.csv")
truth.paragraph_id = truth.paragraph_id.apply(literal_eval)
truth.answers = truth.answers.apply(literal_eval)
questions = pd.read_csv("train_input_question.csv")
for idx in pred.index:
  q_id = pred["question_id"][idx]
  q_rows = questions.loc[questions['id'] == q_id].iloc[-1]
  theme = q_rows["theme"]
  predicted_paragraph = pred["paragraph_id"][idx]
  predicted_ans = pred["answers"][idx]
  
  if theme not in metrics.keys():
    metrics[theme] = {"true_positive": 0, "true_negative": 0, "total_predictions": 0, "f1_sum": 0}

  truth_row = truth.loc[truth['question_id'] == q_id].iloc[-1]
  truth_paragraph_id = [ int(i) for i in truth_row["paragraph_id"] ]
  if predicted_paragraph in truth_paragraph_id:
    # Increase TP for that theme.
    metrics[theme]["true_positive"] = metrics[theme]["true_positive"] + 1
  # -1 prediction in case there is no paragraph which can answer the query.
  if predicted_paragraph == -1 and truth_row["paragraph_id"] == []:
    # Increase TN.
    metrics[theme]["true_negative"] = metrics[theme]["true_negative"] + 1
  # Increase total predictions for that theme.
  metrics[theme]["total_predictions"] = metrics[theme]["total_predictions"] + 1
  f1 = calc_max_f1(predicted_ans, truth_row["answers"])
  
  metrics[theme]["f1_sum"] = metrics[theme]["f1_sum"] + f1

In [ ]:
# NOT allowed to make changes. 

# Final score.
inf_time_threshold = 200.0 # milliseconds.
final_para_score = 0.0
final_qa_score = 0.0
count=0

# Weight would stay hidden from teams.
#theme_weights = {"Kubernetes": 0.5, "ChatGPT": 0.4, "Football world cup": 0.1}

for theme in metrics:
  inf_time_score = 1.0
  metric = metrics[theme]
  para_score = (metric["true_positive"] + metric["true_negative"]) / metric["total_predictions"] 
  qa_score = metric["f1_sum"] / metric["total_predictions"]
  avg_inf_time = theme_inf_time[theme] / metric["total_predictions"]
  if avg_inf_time > inf_time_threshold:
    inf_time_score = inf_time_threshold / avg_inf_time
  #final_qa_score += theme_weights[theme] * inf_time_score * qa_score
  final_qa_score += inf_time_score * qa_score
  #final_para_score += theme_weights[theme] * inf_time_score * para_score
  final_para_score += inf_time_score * para_score
  count+=1

print (final_para_score/count)
print (final_qa_score/count)